# Introduction to Probabilistic Programming

## Introduction



## Preliminaries


### Probability

In [1]:
type Probability = private Probability of double

module Probability =
    let create ( probability : double ) : Probability option =
        if probability >= 0.0 && probability <= 1.0 then Some ( Probability probability )
        else None

    let getProbability ( Probability probability ) = probability

#### Example

In [2]:
// Creating
let prob = Probability.create ( 1.0 / 2.0 )

// Getting the value
match prob with
    | Some p -> Probability.getProbability p
    | None   -> nan

0.5

### Distribution

In [3]:
type Distribution<'T> = seq< 'T * Probability >

#### Uniform Distribution

In [4]:
module UniformDistribution = 

    let private uniformRandomNumberGenerator = System.Random()

    let create ( x : seq< int > ) : Distribution<int>  = 
        seq {
            let countOfSequence = Seq.length x
            let distributionSequence =
                x 
                |> Seq.map( fun e -> e, Probability.create ( 1.0 / double( countOfSequence )))
                |> Seq.filter( fun ( e, p ) -> p.IsSome )
                |> Seq.map( fun (e, p) -> e, p.Value )
            yield! distributionSequence
        }

    let drawOne ( uniformDistribution : Distribution<int> ) : int * Probability = 
        let countOfDistribution = 
            Seq.length uniformDistribution
        let idx = uniformRandomNumberGenerator.Next( 0, countOfDistribution )
        uniformDistribution
        |> Seq.item idx

In [5]:
let diceRollDistribution = UniformDistribution.create [ 1..6 ]
printfn "%A" ( Seq.toList diceRollDistribution )

[(1, Probability 0.1666666667); (2, Probability 0.1666666667);
 (3, Probability 0.1666666667); (4, Probability 0.1666666667);
 (5, Probability 0.1666666667); (6, Probability 0.1666666667)]


In [6]:
printfn "%A" ( UniformDistribution.drawOne diceRollDistribution )

(5, Probability 0.1666666667)


## The Monty Hall Problem

The Monty Hall Problem involves a game show contestent choosing 

In [7]:
type Outcome = Win | Lose
type Door    = A | B | C | NA
let doors    = [ A; B; C ]

In [8]:
type GameState = { winningDoor : Door; chosenDoor : Door; openedDoor : Door }

let start : GameState  = 
    { winningDoor = NA; chosenDoor = NA; openedDoor = NA }

In [9]:
let hidePrize ( state : GameState ) : GameState =
    let winningDoorIdx = fst ( UniformDistribution.drawOne ( UniformDistribution.create [ 1..3 ] )) - 1
    { state with winningDoor = doors.[ winningDoorIdx ] }
    
hidePrize start

{winningDoor = A;
 chosenDoor = NA;
 openedDoor = NA;}

In [10]:
let initializeGame : GameState =
    hidePrize start
    
initializeGame

{winningDoor = B;
 chosenDoor = NA;
 openedDoor = NA;}

In [11]:
let chooseDoor ( state : GameState ) ( door : Door ) : GameState =
    { state with chosenDoor = door }
    
let chooseRandomDoor ( state : GameState ) : GameState =
    let chosenDoorIdx = fst ( UniformDistribution.drawOne (  UniformDistribution.create  [ 1..3 ] )) - 1
    { state with chosenDoor = doors.[ chosenDoorIdx ] }

let chosenRandomDoor = chooseRandomDoor initializeGame
chosenRandomDoor

{winningDoor = B;
 chosenDoor = A;
 openedDoor = NA;}

In [12]:
let openDoor ( state : GameState ) : GameState =
    // Choose the Non-Winning Door that hasn't been chosen by the contestant.
    let doorToOpenAsList = 
        doors 
        |> List.except [ state.winningDoor; state.chosenDoor ]
    let doorToOpen = doorToOpenAsList.[0]
    { state with openedDoor = doorToOpen }
    
let postOpenDoor = openDoor ( chosenRandomDoor )
postOpenDoor

{winningDoor = B;
 chosenDoor = A;
 openedDoor = C;}

In [13]:
type Strategy = GameState -> Outcome

let switch ( state : GameState ) : Outcome =
    let doorToSwitchTo = 
        doors
        |> List.except [ state.chosenDoor; state.openedDoor ]
    if doorToSwitchTo.[0] = state.winningDoor then Win
    else Lose
    
let stay ( state : GameState ) : Outcome = 
    if state.chosenDoor = state.winningDoor then Win
    else Lose

printfn "On Switch: %A" ( switch postOpenDoor )
printfn "On Stay: %A"   ( stay postOpenDoor )

On Switch: Win
On Stay: Lose


In [14]:
let simulateMontyHall ( strategy : Strategy ) : Outcome = 
    let game = 
        initializeGame 
        |> chooseRandomDoor
        |> openDoor
    strategy( game )

simulateMontyHall switch

Win

In [15]:
let generateDistributionOfStaying ( numberOfTrials : int ) : Outcome seq = 
    let mutable list = []
    for i in 1 .. numberOfTrials do
        list <- list @ [ simulateMontyHall stay ] 
    Seq.ofList list

let simulationOfStaying : seq< Outcome > =
    generateDistributionOfStaying 10000

In [16]:
#load "Paket.fsx"

Paket.Package([ "XPlot.Plotly" ])

#load "XPlot.Plotly.fsx"
#load "XPlot.Plotly.Paket.fsx"

open XPlot.Plotly

In [17]:
let winCountOfStaying = 
    simulationOfStaying
    |> Seq.filter( fun x -> x = Win )
    |> Seq.length

let xAxisStaying = [ "Win"; "Loss" ] 
let yAxisStaying = [ winCountOfStaying; ( Seq.length simulationOfStaying - winCountOfStaying )]

let stayingData = List.zip xAxisStaying yAxisStaying

stayingData
|> Chart.Bar
|> Chart.WithHeight 500
|> Chart.WithWidth 700

In [18]:
let generateDistributionOfSwitching ( numberOfTrials : int ) : Outcome list = 
    let mutable list = []
    for i in 1 .. numberOfTrials do
        list <- list @ [ simulateMontyHall switch ] 
    list
    
let simulationOfSwitching = 
    generateDistributionOfSwitching 10000

In [19]:
let winCountOfSwitching = 
    simulationOfSwitching
    |> Seq.filter( fun x -> x = Win )
    |> Seq.length

let xAxisSwitching = [ "Win"; "Loss" ] 
let yAxisSwitching = [ winCountOfSwitching; ( Seq.length simulationOfSwitching - winCountOfSwitching )]

let switchingData = List.zip xAxisSwitching yAxisSwitching

let optionsSwitching =
    Layout( title = "Outcome Count of Switching" )

switchingData
|> Chart.Bar
|> Chart.WithOptions optionsSwitching
|> Chart.WithHeight 500
|> Chart.WithWidth 700

## Bayesian Inference

### A/B Test

In [22]:
let n_visitors_a = 100  // number of visitors shown layout A
let n_conv_a     = 4    // number of vistors shown layout A who converted

let n_visitors_b = 40
let n_conv_b     = 2

In [23]:
let posteriorDistribution ( data         : int           ) 
                          ( priorSampler : seq<double>   ) 
                          ( simulator    : double -> int ) : seq<double option> = 
    seq {
        for p in priorSampler do
            if simulator( p ) = data then yield Some p
            else yield None
    }

In [24]:
open System

let seed   = 123 
let random = Random( seed )

let simulateConversion ( p : double ) ( nVisitors : int ) : int = 
    [ 1..nVisitors ]
    |> List.map( fun x -> random.NextDouble() )
    |> List.filter( fun d -> d < p )
    |> List.sum
    |> int

// Print out the Simulated Conversions.
printfn "%A" ( simulateConversion 0.1 1000 )
printfn "%A" ( simulateConversion 0.1 1000 )
printfn "%A" ( simulateConversion 0.1 1000 )

5
5
4


In [49]:
// [ 0, 1 ]
let uniformPriorSampler : seq< double > =
    seq { while true do yield random.NextDouble() }
    
Seq.take 3 uniformPriorSampler

seq [0.7566052306; 0.4057631983; 0.8549597193]

In [50]:
let applySimulation ( p : double ) ( nVisitors : int ) : int  =
    simulateConversion p nVisitors

In [51]:
let applySimulationA ( p : double ) : int =
    simulateConversion p n_visitors_a
    
let posteriorA = 
    posteriorDistribution n_conv_a uniformPriorSampler applySimulationA
    
let aSamples = 
    posteriorA
    |> Seq.take 10000
    |> Seq.filter( fun x -> x.IsSome )
    |> Seq.map( fun x -> x.Value )

In [52]:
Histogram( x = aSamples )
|> Chart.Plot
|> Chart.WithTitle("Sampled Posterior Distribution A")
|> Chart.WithWidth 700
|> Chart.WithHeight 500

In [53]:
let conversionFractionA = 
    let sumOfASamples = 
        aSamples
        |> Seq.filter( fun x -> x > 0.1 )
        |> Seq.sum
        |> double
    sumOfASamples / double ( Seq.length( aSamples ))

conversionFractionA

0.2923679962

In [54]:
Paket.Package([ "FsLab" ])

#load "FsLab.fsx"

open MathNet.Numerics.Distributions

In [77]:
// Normal Prior Distribution
let normalPriorSampler ( mu : double    ) 
                       ( sigma : double ) : seq< double > =
    let normalDistribution = new Normal( mu, sigma )
    seq { while true do
            let sample : double = normalDistribution.Sample()
            if sample >= 0.0 && sample <= 1.0 then yield sample
            else () }    

let getDefaultNormalPriorSampler : seq<double> = 
    normalPriorSampler 0.1 0.2
    
let getDefaultNormalPriorSamplerSimulate =
    normalPriorSampler 0.1 0.2
    |> Seq.take 10000
    
getDefaultNormalPriorSamplerSimulate

seq [0.04704831195; 0.02705911139; 0.3163468418; 0.1476819897; ...]

In [78]:
let getUniformPriorSamplerSimulate =
    uniformPriorSampler
    |> Seq.take 10000

In [79]:
let overlaidTrace1 =
    Histogram(
        x = getUniformPriorSamplerSimulate,
        opacity = 0.75
    )

let overlaidTrace2 =
    Histogram(
        x = getDefaultNormalPriorSamplerSimulate,
        opacity = 0.75
    )

let overlaidLayout =
    Layout(
        barmode = "overlay",
        title = "Overlaid Histogram"
    )

[overlaidTrace1; overlaidTrace2]
|> Chart.Plot
|> Chart.WithLayout overlaidLayout
|> Chart.WithWidth 700
|> Chart.WithHeight 500

In [81]:
let applySimulationB ( p : double ) : int =
    simulateConversion p n_visitors_b
    
let posteriorB = 
    posteriorDistribution n_conv_b getDefaultNormalPriorSampler applySimulationB

let bSamples = 
    posteriorB
    |> Seq.take 10000
    |> Seq.filter( fun x -> x.IsSome )
    |> Seq.map( fun x -> x.Value )
    
bSamples

seq [0.3522925127; 0.3893903853; 0.4528967751; 0.4150534423; ...]

In [82]:
let overlaidTrace1 =
    Histogram(
        x = aSamples,
        opacity = 0.75
    )

let overlaidTrace2 =
    Histogram(
        x = bSamples,
        opacity = 0.75
    )

let overlaidLayout =
    Layout(
        barmode = "overlay",
        title = "Overlaid Histogram"
    )

[overlaidTrace1; overlaidTrace2]
|> Chart.Plot
|> Chart.WithLayout overlaidLayout
|> Chart.WithWidth 700
|> Chart.WithHeight 500